# TP3 Kernel Methods for Machine Learning

Written by Yunlong Jiao, 27 Jan 2019

In [1]:
# setup
import numpy as np
from sklearn import linear_model as lm

In [2]:
import sys
print(sys.version)

3.6.6 |Anaconda, Inc.| (default, Jun 28 2018, 11:07:29) 
[GCC 4.2.1 Compatible Clang 4.0.1 (tags/RELEASE_401/final)]


In [3]:
import sklearn
sklearn.__version__

'0.19.2'

## Tasks

1. Implement (naive) solvers to Ridge Regression, Weighted Ridge Regression and Logistic Ridge Regression (using Iteratively Reweighted Least Squares). See notes for the mathematical derivation.
2. Simulate some toy data to check if our solvers give correct solutions as provided by R.

## Solutions

**Ridge Regression (RR)**

Given $X \in \mathbb{R}^{n \times p}$ and $y \in \mathbb{R}^n$, solve
$$
\min_{\beta \in \mathbb{R}^p} \frac{1}{n} \|y - X \beta\|^2 + \lambda \|\beta\|^2 \,.
$$

In [4]:
# Ridge Regression (RR)
def solveRR(y, X, lam):
    n,p = X.shape
    assert (len(y) == n)
    
    A = X.T @ X
    # Adjust diagonal due to Ridge
    A[np.diag_indices_from(A)] += lam*n
    b = X.T.dot(y)
    
    # Find solution to the linear system Ax = b
    beta = np.linalg.solve(A,b)
    return (beta)

**Weighted Ridge Regression (WRR)**

Given $X \in \mathbb{R}^{n \times p}$ and $y \in \mathbb{R}^n$, and weights $w \in \mathbb{R}^n_+$, solve
$$
\min_{\beta \in \mathbb{R}^p} \frac{1}{n} \sum_{i=1}^n w_i (y_i - \beta^\top x_i)^2 + \lambda \|\beta\|^2 \,.
$$

In [5]:
# Weighted Ridge Regression (WRR)
def solveWRR(y, X, w, lam):
    y1 = np.sqrt(w)*y
    X1 = (np.sqrt(w)*X.T).T
    
    beta = solveRR(y1, X1, lam)
    return (beta)

**Logistic Ridge Regression (LRR)**

Given $X \in \mathbb{R}^{n \times p}$ and $y \in \{-1,+1\}^n$, solve
$$
\min_{\beta \in \mathbb{R}^p} \frac{1}{n} \sum_{i=1}^n \log (1+e^{-y_i \beta^\top x_i}) + \lambda \|\beta\|^2 \,.
$$

In [6]:
# Logistic Ridge Regression (LRR)
def solveLRR(y, X, lam):
    # Parameters
    L = 100
    eps = 1e-3
    sigmoid = lambda a: 1/(1+np.exp(-a))
    n,p = X.shape
    
    # Initialize
    beta = np.zeros(p)
    
    # Update (equiv to IRLS)
    for k in range(L):
        beta_old = beta
        f = X.dot(beta_old)
        w = sigmoid(f) * sigmoid(-f)
        z = f + y / sigmoid(y*f)
        beta = solveWRR(z, X, w, 2*lam)
        if np.sum((beta-beta_old)**2) < eps:
            break
        
    return (beta)

**Toy experiments**

In [7]:
# Toy data
np.random.seed(12345)
n = 100
p = 20
X = np.random.normal(0,1,(n,p))
X = sklearn.preprocessing.scale(X)
y = np.sign(np.random.normal(0,1,n))
lam = 0.01

# Our solver
beta1 = solveRR(y, X, lam) # RR
# beta1 = solveLRR(y, X, lam) # LRR
# print(beta1)

# Python solver
beta2 = lm.Ridge(alpha=lam*n,fit_intercept=False,normalize=False).fit(X, y).coef_ # RR
# beta2 = lm.RidgeClassifier(alpha=2*n*lam,fit_intercept=False,normalize=False).fit(X, y).coef_ # LRR gives different results?
# print(beta2)

# Check
np.sum((beta1-beta2)**2)

2.0619487467095844e-32